Реализация метода оценки уверенности бустинга.

Введем такое понятие как виртуальный ансамбль. Возьмём частичное предсказание на i-ом шаге (предсказание первых i деревьев). Будем использовать i = N/2 как первую модель, i = N/2 + k как вторую, i = N/2 + 2k как третью и так далее. Теперь мы можем оценивать неуверенность модели как разброс (Variance) между предсказаниями моделей виртуального ансамбля.

Сначала реализуем наиболее популярные метрики (MAPE, sMAPE, WAPE, Bias), используемые в задаче предсказания спроса.

In [21]:
import warnings
warnings.filterwarnings('ignore')

import numpy as np

def mape(y_true: np.ndarray, y_pred: np.ndarray) -> float:
    mape = np.mean(np.abs((y_true - y_pred) / y_true))
    return mape

def smape(y_true: np.array, y_pred: np.array) -> float:
    if np.array_equal((y_true == 0), y_pred == 0):
        y_new = np.where(y_pred == 0, 1, y_pred)
        return 100/len(y_true) * np.sum(2 * np.abs(y_pred - y_true) / (np.abs(y_true) + np.abs(y_new)))
    return 100/len(y_true) * np.sum(2 * np.abs(y_pred - y_true) / (np.abs(y_true) + np.abs(y_pred)))

def wape(y_true: np.ndarray, y_pred: np.ndarray) -> float:
    return np.sum(np.abs(y_true - y_pred))/np.sum(y_true)

def bias(y_true: np.ndarray, y_pred: np.ndarray) -> float:
    return np.sum(y_true - y_pred)/np.sum(y_true)

Time-Series Validation

После получение нужного датасета, нам требуется оценить точность моделей.
Посмотрите исходный код библиотеки sklearn и напишите свой класс GroupTimeSeriesSplit, который будет выполнять верную Time-Series валидацию.

Поэкспериментируйте с кросс-валидацией, пробуя разные модели. Выберите модель, которая даёт лучшую метрику WAPE.

In [9]:
from splitter import PurgedGroupTimeSeriesSplit #код реализован в отдельном файле.
from sklearn.preprocessing import StandardScaler
import pandas as pd

# Data loading
df = pd.read_csv('features.csv', parse_dates=["monday"])

y = df.pop("y")

# monday or product_name as a groups for validation?
groups = df["product_name"]
df.drop(["product_name", "monday"], axis=1, inplace=True)

X = df

cv = PurgedGroupTimeSeriesSplit(n_splits=5,
    max_train_group_size=15, group_gap=5, max_test_group_size=5)

In [11]:
from sklearn.ensemble import GradientBoostingRegressor

scores = []

for train_idx, test_idx in cv.split(X, groups=groups):
    # Split train/test
    # Fit model
    x0, x1 = X.loc[train_idx], X.loc[test_idx]
    y0, y1  = y.loc[train_idx], y.loc[test_idx]
    
    scaler = StandardScaler()
    x0 = scaler.fit_transform(x0)
    x1 = scaler.transform(x1)
    
    model = GradientBoostingRegressor()
    model.fit(x0, y0)
    # Predict and print metrics
    y_pred = model.predict(x1)
    score = wape(y1, y_pred)
    scores.append(score)
print(np.mean(scores))

0.12770079433024306


In [12]:
from lightgbm import LGBMRegressor
scores = []

for train_idx, test_idx in cv.split(X, groups=groups):
    # Split train/test
    # Fit model
    x0, x1 = X.loc[train_idx], X.loc[test_idx]
    y0, y1  = y.loc[train_idx], y.loc[test_idx]
    
    scaler = StandardScaler()
    x0 = scaler.fit_transform(x0)
    x1 = scaler.transform(x1)
    
    model = LGBMRegressor()
    model.fit(x0, y0)
    # Predict and print metrics
    y_pred = model.predict(x1)
    score = wape(y1, y_pred)
    scores.append(score)
print(np.mean(scores))

0.1250218762511904


In [5]:
from sklearn.ensemble import RandomForestRegressor

scores = []

for train_idx, test_idx in cv.split(X, groups=groups):
    # Split train/test
    # Fit model
    x0, x1 = X.loc[train_idx], X.loc[test_idx]
    y0, y1  = y.loc[train_idx], y.loc[test_idx]
    
    model = RandomForestRegressor()
    model.fit(x0, y0)
    # Predict and print metrics
    y_pred = model.predict(x1)
    score = wape(y1, y_pred)
    scores.append(score)
print(np.mean(scores))

0.1307295988768619


In [14]:
from catboost import CatBoostRegressor

scores = []

for train_idx, test_idx in cv.split(X, groups=groups):
    # Split train/test
    # Fit model
    x0, x1 = X.loc[train_idx], X.loc[test_idx]
    y0, y1  = y.loc[train_idx], y.loc[test_idx]
    
    scaler = StandardScaler()
    x0 = scaler.fit_transform(x0)
    x1 = scaler.transform(x1)
    
    model = CatBoostRegressor(verbose=False)
    model.fit(x0, y0)
    # Predict and print metrics
    y_pred = model.predict(x1)
    score = wape(y1, y_pred)
    scores.append(score)
print(np.mean(scores))

0.1304528928030768


In [15]:
from xgboost import XGBRegressor

scores = []

for train_idx, test_idx in cv.split(X, groups=groups):
    # Split train/test
    # Fit model
    x0, x1 = X.loc[train_idx], X.loc[test_idx]
    y0, y1  = y.loc[train_idx], y.loc[test_idx]
    
    scaler = StandardScaler()
    x0 = scaler.fit_transform(x0)
    x1 = scaler.transform(x1)
        
    model = XGBRegressor()
    model.fit(x0, y0)
    # Predict and print metrics
    y_pred = model.predict(x1)
    score = wape(y1, y_pred)
    scores.append(score)
print(np.mean(scores))

0.1331049149592444


Лучшей моделью оказался LGBMRegressor. Попробуем его улучшить с помощью GridSearchCV.

In [38]:
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import make_scorer
my_scorer = make_scorer(wape, greater_is_better=False) #создаём свою метрику для валидации на основе wape

X_train, X_test, y_train, y_test, groups_train, groups_test = train_test_split(X, y, groups, test_size=0.33, 
                                                                               random_state=42, shuffle=False)

scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

lgb_model = LGBMRegressor()

parameters = {
     'num_iterations': [1500, 2000, 5000],
     'learning_rate':[0.05, 0.005],
    'num_leaves':[7, 15, 31 ],
    'max_depth' :[10, 15, 25],
    'min_data_in_leaf':[15,25 ],
   'feature_fraction': [0.6, 0.8,  0.9],
     'bagging_fraction': [0.6, 0.8],
     'bagging_freq': [100, 200, 400],     
 }

lgb_grid = GridSearchCV(lgb_model,
                        parameters,
                        scoring = my_scorer,
                        cv = cv.split(X_train, groups=groups_train),
                        verbose=False)

lgb_grid.fit(X_train, y_train)

print(lgb_grid.best_score_)
print(lgb_grid.best_params_)

[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=15, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=15
[LightGBM] [Warning] bagging_fraction is set=0.6, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6
[LightGBM] [Warning] bagging_freq is set=100, subsample_freq=0 will be ignored. Current value: bagging_freq=100
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=15, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=15
[LightGBM] [Warning] bagging_fraction is set=0.6, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6
[LightGBM] [Warning] bagging_freq is set=100, subsample_freq=0 will be ignored. Current value: bagging_freq=100
[LightGBM] [Warning] feature_fraction is set=0.6, 

[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=15, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=15
[LightGBM] [Warning] bagging_fraction is set=0.6, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6
[LightGBM] [Warning] bagging_freq is set=100, subsample_freq=0 will be ignored. Current value: bagging_freq=100
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=15, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=15
[LightGBM] [Warning] bagging_fraction is set=0.6, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6
[LightGBM] [Warning] bagging_freq is set=100, subsample_freq=0 will be ignored. Current value: bagging_freq=100
[LightGBM] [Warning] feature_fraction is set=0.6, 

[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=15, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=15
[LightGBM] [Warning] bagging_fraction is set=0.6, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6
[LightGBM] [Warning] bagging_freq is set=100, subsample_freq=0 will be ignored. Current value: bagging_freq=100
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=15, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=15
[LightGBM] [Warning] bagging_fraction is set=0.6, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6
[LightGBM] [Warning] bagging_freq is set=100, subsample_freq=0 will be ignored. Current value: bagging_freq=100
[LightGBM] [Warning] feature_fraction is set=0.6, 

[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=25, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=25
[LightGBM] [Warning] bagging_fraction is set=0.6, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6
[LightGBM] [Warning] bagging_freq is set=100, subsample_freq=0 will be ignored. Current value: bagging_freq=100
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=25, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=25
[LightGBM] [Warning] bagging_fraction is set=0.6, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6
[LightGBM] [Warning] bagging_freq is set=100, subsample_freq=0 will be ignored. Current value: bagging_freq=100
[LightGBM] [Warning] feature_fraction is set=0.6, 

[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=25, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=25
[LightGBM] [Warning] bagging_fraction is set=0.6, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6
[LightGBM] [Warning] bagging_freq is set=100, subsample_freq=0 will be ignored. Current value: bagging_freq=100
[LightGBM] [Warning] feature_fraction is set=0.6, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.6
[LightGBM] [Warning] min_data_in_leaf is set=25, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=25
[LightGBM] [Warning] bagging_fraction is set=0.6, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6
[LightGBM] [Warning] bagging_freq is set=100, subsample_freq=0 will be ignored. Current value: bagging_freq=100
[LightGBM] [Warning] feature_fraction is set=0.6, 

...

[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] min_data_in_leaf is set=15, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=15
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=400, subsample_freq=0 will be ignored. Current value: bagging_freq=400
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] min_data_in_leaf is set=15, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=15
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=400, subsample_freq=0 will be ignored. Current value: bagging_freq=400
[LightGBM] [Warning] feature_fraction is set=0.9, 

[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] min_data_in_leaf is set=15, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=15
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=400, subsample_freq=0 will be ignored. Current value: bagging_freq=400
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] min_data_in_leaf is set=15, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=15
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=400, subsample_freq=0 will be ignored. Current value: bagging_freq=400
[LightGBM] [Warning] feature_fraction is set=0.9, 

[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] min_data_in_leaf is set=15, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=15
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=400, subsample_freq=0 will be ignored. Current value: bagging_freq=400
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] min_data_in_leaf is set=25, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=25
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=400, subsample_freq=0 will be ignored. Current value: bagging_freq=400
[LightGBM] [Warning] feature_fraction is set=0.9, 

[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] min_data_in_leaf is set=25, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=25
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=400, subsample_freq=0 will be ignored. Current value: bagging_freq=400
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] min_data_in_leaf is set=25, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=25
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=400, subsample_freq=0 will be ignored. Current value: bagging_freq=400
[LightGBM] [Warning] feature_fraction is set=0.9, 

[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] min_data_in_leaf is set=25, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=25
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=400, subsample_freq=0 will be ignored. Current value: bagging_freq=400
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] min_data_in_leaf is set=25, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=25
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=400, subsample_freq=0 will be ignored. Current value: bagging_freq=400
[LightGBM] [Warning] feature_fraction is set=0.9, 

In [ ]:
best_model = LGBMRegressor(**lgb_grid.best_params_)
best_model.fit(X_train, y_train)

In [48]:
best_model.booster_.save_model("lgb.model")

In [41]:
y_pred = best_model.predict(X_test)
print(wape(y_test, y_pred))

0.03867966340086979


Вам необходимо написать 3 функции, каждая из которых принимает на вход обученную модель и датасет (model и Х), на выходе, соответственно:
________________________________________
1.	Сколько первых деревьев включено в каждую модель виртуального ансамбля.

2.	Предсказание каждой модели виртуального ансамбля.

3.	Итоговое предсказание по каждому объекту и оценка неуверенности на каждом объекте.

Возьмём частичное предсказание на i-ом шаге (предсказание первых i деревьев). Будем использовать i = N/2 как первую модель, i = N/2 + k как вторую, i = N/2 + 2k как третью и так далее. 

In [42]:
from dataclasses import dataclass
from typing import List

import numpy as np

def virtual_ensemble_iterations(
    model: GradientBoostingRegressor, k: int = 20
) -> List[int]:
    '''Функция даёт ответ на вопрос, сколько первых деревьев 
    включать в каждую модель виртуального ансамбля. Принимает на вход только модель и шаг'''
    N = model.n_estimators-1
    iterations = []
    iteration = N//2
    i = 1
    while iteration < N:
        iterations.append(iteration)
        iteration = N//2+k*i
        i+=1   
    return iterations

In [86]:
# для других моделей можно было бы использовать staged_predict, но в LGBM этой функции нет, поэтому придётся выдумать костыль.

def virtual_ensemble_predict(
    model: GradientBoostingRegressor, X: np.ndarray, y: np.ndarray, k: int = 20
) -> np.ndarray:
    '''Функция отдает предсказания для каждого объекта из X для каждой 
    модели виртуального ансамбля в виде матрицы размера (N, K), 
    где N – число строк в X, а K – количество моделей в виртуальном ансамбле.'''
    models = virtual_ensemble_iterations(model, k)
    params = model.get_params()
    N = len(X)
    K = len(models)
    stage_preds = np.zeros((N, K))
    
    for i in range(K):
        params['n_estimators'] = models[i]  
        mod = type(model)(**params)
        mod.fit(X, y)
        stage_preds[:, i] = mod.predict(X)    
    return stage_preds

In [87]:
from dataclasses import dataclass

@dataclass
class PredictionDict:
    ''' 1. pred: матрица предсказание исходного бустинга.
        2. uncertainty: "уверенность" модели на каждом объекте во время предсказания.
        3. pred_virt: усреднение предсказаний моделей виртуального ансамбля.
        4. lcb: pred_virt−3⋅uncertainty.
        5. ucb: pred_virt+3⋅uncertainty.
        '''
    pred: np.ndarray = np.array([])
    uncertainty: np.ndarray = np.array([])
    pred_virt: np.ndarray = np.array([])
    lcb: np.ndarray = np.array([])
    ucb: np.ndarray = np.array([])

In [88]:
def predict_with_uncertainty(
    model: GradientBoostingRegressor, X: np.ndarray, y: np.ndarray, k: int = 20
) -> PredictionDict:
    '''Функция возвращает объект PredictionDict'''
    pred = model.predict(X)
    stage_preds = virtual_ensemble_predict(model, X, y, k)
    uncertainty = np.std(stage_preds, axis=0)
    pred_virt = np.mean(stage_preds, axis=0)
    lcb = pred_virt-3*uncertainty
    ucb = pred_virt+3*uncertainty
    prediction_dict = PredictionDict(pred, uncertainty, pred_virt, lcb, ucb)
    return prediction_dict

In [89]:
predict_with_uncertainty(best_model, X_train, y_train, 20)

[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] min_data_in_leaf is set=15, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=15
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=100, subsample_freq=0 will be ignored. Current value: bagging_freq=100
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] min_data_in_leaf is set=15, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=15
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=100, subsample_freq=0 will be ignored. Current value: bagging_freq=100
[LightGBM] [Warning] feature_fraction is set=0.9, 

PredictionDict(pred=array([ 1.98847901, 17.06702601, 21.03215836, ...,  1.15978303,
       19.87082742, 11.98380864]), uncertainty=array([12.34610379, 12.34610379, 12.34610379]), pred_virt=array([20.95016412, 20.95016412, 20.95016412]), lcb=array([-16.08814726, -16.08814726, -16.08814726]), ucb=array([57.98847549, 57.98847549, 57.98847549]))